# Target and Data Drift Iris Dataset

In [1]:
! pip3 install pandas
! pip3 install evidently
! pip3 install minio

In [2]:
from minio import Minio
from minio.error import ResponseError
from dotenv import load_dotenv
load_dotenv()

import pandas as pd

from sklearn import datasets

from evidently.dashboard import Dashboard
from evidently.dashboard.tabs import DataDriftTab, CatTargetDriftTab

from evidently.model_profile import Profile
from evidently.model_profile.sections import DataDriftProfileSection, CatTargetDriftProfileSection 

In [ ]:
# Get environment variables
ACCESS_KEY = os.getenv('ACCESS_KEY')
SECRET_KEY = os.getenv('SECRET_KEY')

In [ ]:
client = Minio(
    "10.0.105.60:9000",
    access_key=ACCESS_KEY,
    secret_key=SECRET_KEY,
    secure=False
)

# Make 'evidently' bucket if not exist.
found = client.bucket_exists("evidently")
if not found:
    client.make_bucket("evidently")
else:
    print("Bucket 'evidently' already exists")

# load CSV Data from MinIO
try:
    client.fget_object('database', 'influxDataLast1Days.csv', './influxDataLast1Days.csv')
    client.fget_object('database', 'influxDataLast30Days.csv', './influxDataLast30Days.csv')
except ResponseError as err:
    print(err)

In [3]:
import warnings
warnings.filterwarnings('ignore')
warnings.simplefilter('ignore')

## Iris Data

In [4]:
iris_frame = pd.read_csv('influxDataLast30Days.csv')
iris_frame

FileNotFoundError: [Errno 2] No such file or directory: 'influxDataLast30Days.csv'

In [ ]:
iris_frame['target'] = iris_frame.occupancy

In [ ]:
current = int(len(iris_frame.index) * 0.03)
current

1086

# Target and Data Drift Dashboard

In [ ]:
iris_data_and_target_drift_dashboard = Dashboard(tabs=[DataDriftTab(verbose_level=0), 
                                                       CatTargetDriftTab(verbose_level=0)])

In [ ]:
iris_data_and_target_drift_dashboard.calculate(iris_frame[:current], iris_frame[current:], column_mapping=None)

In [ ]:
iris_data_and_target_drift_dashboard.show()

In [ ]:
iris_data_and_target_drift_dashboard.save('index.html')

In [ ]:

# load HTML file to MinIO
client.fput_object(
    "evidently", "index.html", "./index.html",
)
print(
    "HTML file is successfully uploaded to bucket 'evidently'."
)